# Sattelzeit comparisons

In [1]:
from ipynb.fs.full.koselleck import *

[Koselleck] (07:24:11) Alles bereit 


In [2]:

def get_top_changes_stz(n=200,sby='(III)'):
    odf=get_tilts_sattelzeit().groupby(['vector','word']).mean()
    odf=odf.sort_values(['vector',sby],ascending=[1,0])
    od={}
    for vec,vecdf in odf.groupby('vector'):
        posneg=vec.split('.')[0].split('-')
        pos,neg=posneg if len(posneg)==2 else (posneg[0],posneg[0])
        od[f'+{pos}']=vecdf.sort_values(sby,ascending=False).head(n).index.get_level_values('word')
        od[f'+{neg}' if pos!=neg else f'-{neg}']=vecdf.sort_values(sby,ascending=True).head(n).index.get_level_values('word')
    return od

In [3]:
# get_top_changes_stz()

In [4]:
# get_top_changes_stz(n=None)

In [5]:
get_

NameError: name 'get_' is not defined

In [ ]:
def get_topmost_change(sby='(III)',cutoff=.5):
    sdf=get_tilts_sattelzeit().sort_values(['word','abs(III)'],ascending=[1,0])
    sdf1=sdf.groupby('word').head(1).reset_index()
    def class_change(row):
        vec=row.vector.split('.')[0]
        va,vb=vec.split('-') if '-' in vec else (vec,vec)
#         print(vec,va,vb)
        if row[sby]>cutoff:
            return '+'+va
        elif row[sby]<-cutoff:
            return '+'+vb if va!=vb else '-'+va
        else:
            return ''

    sdf1['change']=sdf1.apply(class_change,axis=1)
    sdf1=sdf1.set_index('word')
    return sdf1

DFALLSGNCH=None
def get_all_signif_changes(cutoff=.5,sby='(III)'):
    global DFALLSGNCH
    if DFALLSGNCH is None:
        sdf=get_tilts_sattelzeit().sort_values(['word','abs(III)'],ascending=[1,0])
        sdf1=sdf.reset_index()
        sdf1['change']=sdf1.apply(class_change,axis=1)
        sdf1=sdf1.set_index('word')
        DFALLSGNCH=sdf1[sdf1.change!='']
    return DFALLSGNCH


In [ ]:
# get_avg_selfdists()

In [ ]:
get_changeranks_sattelzeit()

In [ ]:
def get_all_word_rankings():
    odf=pd.DataFrame()
    rankings = get_top_changes_stz(n=None)
    for ranking,rdata in rankings.items():
        s=pd.Series(list(range(len(rdata))), index=rdata) + 1
        odf[ranking]=s
    odf['+LNMSz']=get_changeranks_sattelzeit().rank_word
    odf['+LNM']=get_avg_selfdists().selfdist_rank
    odf['+Nov'] = get_all_novelty_scores().groupby('word'
    ).quantile(.75).foote_novelty_z.rank(ascending=False)
    return odf

In [ ]:
dfranks=get_all_word_rankings()
dfranks

In [ ]:
dfranks.loc['station']

In [ ]:
dfranks.corr().sort_values('+LNM',ascending=False)

In [ ]:
start_fig(
    dfranks.reset_index().sample(n=500),
    x='+LNM',
    y='+Nov',
    label='word',
) + p9.geom_smooth() + p9.geom_text(size=5)

In [ ]:
def get_invalid_words():
    dfanno=get_dfanno()
    return set(dfanno[dfanno.is_valid.str.startswith('n')].index)


In [ ]:
get_all_word_rankings().mean(axis=1).sort_values()

In [ ]:
# len(get_invalid_words())x

In [ ]:
dftop = dfranks.sort_values('+LNM')[:1000]
dftop

In [ ]:
# len(invalid_words)

In [ ]:
def to_grp(x):
    if x>=90: return '++Changed'
#     if x>=75: return '75-90%'
    if x<=10: return '--Changed'
#     if x<=25: return '10-25%'
#     return '25-75%'
    return '==Changed'
# def z2grp(x):
#     if x>2: return '++Changed'
#     if x<-2: return '--Changed'
#     return '==Changed'

dfrank_lnm = get_changeranks_sattelzeit()
dfrank_lnm['perc_grp']=dfrank_lnm.lnm_perc_word.apply(to_grp)
dfrank_lnm=dfrank_lnm[dfrank_lnm.perc_grp!='==Changed']
# dfrank_lnm['perc_grp']=dfrank_lnm.lnm_z.apply(z2grp)
d=lltk.get_word2pos()
dfrank_lnm['pos']=[d.get(x,'')[:1] for x in dfrank_lnm.index]
dfrank_lnm

In [ ]:
invalidwords=get_invalid_words() | {
    'loll','truss','tome','ads','invalids','foil'
}
gby=['perc_grp','pos']
lim=50
dfsmpl=pd.DataFrame([
    {
        gby[0]:i[0],
        gby[1]:i[1],
        'neighb_str':', '.join([
#             f'{i}. {x}' if x not in invalidwords else f'{i}. ~~{x}~~'
            f'{x}' if x not in invalidwords else f'~~{x}~~'
            for i,x in enumerate(gdf.sort_values(
                'lnm_perc_word',ascending=not i[0].startswith('+')
            ).index)
            if x not in invalidwords
            and 'f' not in x 
            and 's' not in x
        ][:lim])
    }
    for i,gdf in dfrank_lnm.groupby(gby)
])
odf=dfsmplpiv=dfsmpl.pivot('pos','perc_grp','neighb_str').T#.sort_index(ascending=False)
odf.index=["Significant change (>90%)", "Significant stability (<10%)"]
odf.columns = ['Adjectives','Nouns','Verbs']
odf=odf.rename_axis('Degree of change').T
printm(odf)

In [ ]:
# imgkit.from_string??

In [ ]:
def df_to_png(df,ofn='fig.dataframe.png',style=None,force_html=True,replaced={}):
    import imgkit
    
    STYLE="""
        table { border:1px dotted silver; }
        td,th { font-family: "Baskerville", "Libre Baskerville", "Georgia", serif; }
        tbody tr:nth-child(even)   { background-color:#eee; }
        tbody tr:nth-child(odd)    { background-color:#fff; }
        thead { background-color:#ddd; }
    """
    style = STYLE if not style else style
    style=f'<style type="text/css">{style}</style>'    
    ohtml=df.to_html()
    if force_html: ohtml=ohtml.replace('&gt;','>').replace('&lt;','<')
    for k,v in replaced.items(): ohtml=ohtml.replace(k,v)
    o='<html><body>'+style + ohtml+'</body></html>'
    imgkit.from_string(o, ofn, options={'--quiet':''})
    print_img(ofn)
    return ofn

In [ ]:
# !wkhtmltopdf --help

In [ ]:
get_nbr_simple_sattelzeit('station')

In [ ]:
# df_to_png(odf, os.path.join(PATH_FIGS2,'fig.df.bigchanges.v3.png'))

In [ ]:
posd=dict(j='Adjective',n='Noun',v='Verb')

def plot_nbr_simple_sattelzeit(words,vnum='eg3',lim=25,add_pos=False,sort_orig=False):
    words=tokenize_fast(words) if type(words)==str else words
    odf2=get_nbr_simple_sattelzeit(words,html=False,lim=lim).rename_axis('Word')
    if sort_orig:
        odf2['_']=[words.index(x) for x in odf2.index]
        odf2=odf2.sort_values('_').drop('_',1)
    if add_pos:
        odf2=odf2.reset_index()
        odf2['POS']=[posd.get(lltk.get_word2pos().get(x,' ')[0],'') for x in odf2.Word]
        odf2=odf2.set_index(['POS','Word']).rename_axis(['','Word'])
    odf2=odf2.applymap(lambda x: x if type(x)==str else f'{x:.0f}')
    ofn2=os.path.join(PATH_FIGS2,f'df.nbr_simple.{vnum}.png')
    return df_to_png(odf2,ofn2,replaced={'**':''})

In [ ]:
plot_nbr_simple_sattelzeit('radical local   station drawback  recalling embracing',
                           lim=10,vnum='eg5-11',
                          sort_orig=True,add_pos=True)

In [ ]:
plot_nbr_simple_sattelzeit('culture liberal liberty',lim=25,
                           vnum='eg-f13-v2')

In [ ]:
printm(get_nbr_simple_sattelzeit('veiled,effective,radical,rail,drawbacks,cconsiders,defied,fume'))

In [ ]:
stop

In [ ]:
# o=odf.style.set_properties(**{'width': '300px'})
# printm(odf)

In [ ]:
import dataframe_image as dfi

In [ ]:
# dfi.export??

In [ ]:
ofn1=os.path.join(PATH_FIGS2,'fig.bigchanges_table.png')
dfi.export(o, ofn1, table_conversion='matplotlib')

In [ ]:
print_img(ofn1)

In [ ]:
# sys.path.append('../../abslithist/')
# import abslithist as alh

In [ ]:
# !pip install mpi_slingshot

In [ ]:
dict(zip([1,2,3],['a','b','c']))

In [ ]:
dfsmpl

In [ ]:
stop

In [ ]:
dfranks.loc[['culture','liberal','liberty']].T.sort_values('+LNM',1)

In [ ]:
dfrankcorrs=dfranks.corr().reset_index().melt(id_vars='index').query('-.99<value<.99').sort_values('value',ascending=False)
dfrankcorrs

In [ ]:
# !pip install factor_analyzer

In [ ]:
from factor_analyzer import FactorAnalyzer

In [ ]:
fa=FactorAnalyzer(rotation=None,n_factors=10)

In [ ]:
fa.fit(dfranks)

In [ ]:
# commd=pd.Series(fa.get_communalities(), index=dfranks.columns).sort_values()
# commd

In [ ]:
ldf=pd.DataFrame(fa.loadings_,index=dfranks.columns)
ldf

In [ ]:
import plotly.express as px

In [ ]:
# px.scatter(ldf.reset_index(),x=0,y=1,text='index')

In [ ]:
# import plotly.figure_factory as ff
# fig=ff.create_dendrogram(ldf, labels=ldf.index, orientation='left')
# fig.update_layout(height=900,width=600)
# fig.show()

In [ ]:
# from scipy.cluster import hierarchy

In [ ]:
# Z = hierarchy.linkage(ldf)
# plt.figure()
# dn= hierarchy.dendrogram(Z)

In [ ]:
ldf

In [ ]:
# pd.DataFrame(Z,index=ldf.iloc[:-1].index)

In [ ]:
dfanno=get_dfanno()
invalid_words = set(dfanno[
    dfanno.is_valid.str.startswith('n')
].index)

In [ ]:
def show_top_word_rankings(n=25):
    df=get_all_word_rankings()
    df=df.loc[set(df.index) - set(invalid_words)]
    odf=pd.DataFrame([
        {'vector':col,
        'top':', '.join(df[col].sort_values().index[:n])
        } for col in df.columns
    ])
    return odf

In [ ]:
show_top_word_rankings()